In [1]:
%matplotlib inline
import numpy as np
import pandas as pd
import scipy
import sklearn
import spacy
import matplotlib.pyplot as plt
import seaborn as sns
import re
from nltk.corpus import gutenberg, stopwords
from collections import Counter
import nltk

nltk.download('gutenberg')
!python -m spacy download en

[nltk_data] Downloading package gutenberg to
[nltk_data]     C:\Users\catan\AppData\Roaming\nltk_data...
[nltk_data]   Package gutenberg is already up-to-date!


[+] Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')
[x] Couldn't link model to 'en'
Creating a symlink in spacy/data failed. Make sure you have the required
permissions and try re-running the command as admin, or use a virtualenv. You
can still import the model as a module and call its load() method, or create the
symlink manually.
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\en_core_web_sm -->
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\spacy\data\en
[!] Download successful but linking failed
Creating a shortcut link for 'en' didn't work (maybe you don't have admin
permissions?), but you can still load the model via its full package name: nlp =
spacy.load('en_core_web_sm')


You should consider upgrading via the 'python -m pip install --upgrade pip' command.
You do not have sufficient privilege to perform this operation.


Supervised NLP requires a pre-labelled dataset for training and testing, and is generally interested in categorizing text in various ways. In this case, we are going to try to predict whether a sentence comes from _Alice in Wonderland_ by Lewis Carroll or _Persuasion_ by Jane Austen. We can use any of the supervised models we've covered previously, as long as they allow categorical outcomes. In this case, we'll try Random Forests, SVM, and KNN.

Our feature-generation approach will be something called _BoW_, or _Bag of Words_. BoW is quite simple: For each sentence, we count how many times each word appears. We will then use those counts as features.

**Note**: Since processing all the text takes around ~5-10 minutes, in the cell below we are taking only the first tenth of each text. If you want to experiment, feel free to change the following code in the next cell:

```python
alice = text_cleaner(alice[:int(len(alice)/10)])
persuasion = text_cleaner(persuasion[:int(len(persuasion)/10)])
```
to 

```python
alice = text_cleaner(alice)
persuasion = text_cleaner(persuasion)
```

In [2]:
import os
import nltk.corpus
print(os.listdir(nltk.data.find("corpora")))

['abc', 'abc.zip', 'alpino', 'alpino.zip', 'biocreative_ppi', 'biocreative_ppi.zip', 'brown', 'brown.zip', 'brown_tei', 'brown_tei.zip', 'cess_cat', 'cess_cat.zip', 'cess_esp', 'cess_esp.zip', 'chat80', 'chat80.zip', 'city_database', 'city_database.zip', 'cmudict', 'cmudict.zip', 'comparative_sentences', 'comparative_sentences.zip', 'comtrans.zip', 'conll2000', 'conll2000.zip', 'conll2002', 'conll2002.zip', 'conll2007.zip', 'crubadan', 'crubadan.zip', 'dependency_treebank', 'dependency_treebank.zip', 'dolch', 'dolch.zip', 'europarl_raw', 'europarl_raw.zip', 'floresta', 'floresta.zip', 'framenet_v15', 'framenet_v15.zip', 'framenet_v17', 'framenet_v17.zip', 'gazetteers', 'gazetteers.zip', 'genesis', 'genesis.zip', 'gutenberg', 'gutenberg.zip', 'ieer', 'ieer.zip', 'inaugural', 'inaugural.zip', 'indian', 'indian.zip', 'jeita.zip', 'kimmo', 'kimmo.zip', 'knbc.zip', 'lin_thesaurus', 'lin_thesaurus.zip', 'machado.zip', 'mac_morpho', 'mac_morpho.zip', 'masc_tagged.zip', 'movie_reviews', 'movie

In [3]:
nltk.corpus.gutenberg.fileids()

['austen-emma.txt',
 'austen-persuasion.txt',
 'austen-sense.txt',
 'bible-kjv.txt',
 'blake-poems.txt',
 'bryant-stories.txt',
 'burgess-busterbrown.txt',
 'carroll-alice.txt',
 'chesterton-ball.txt',
 'chesterton-brown.txt',
 'chesterton-thursday.txt',
 'edgeworth-parents.txt',
 'melville-moby_dick.txt',
 'milton-paradise.txt',
 'shakespeare-caesar.txt',
 'shakespeare-hamlet.txt',
 'shakespeare-macbeth.txt',
 'whitman-leaves.txt']

In [4]:
# Utility function for standard text cleaning.
def text_cleaner(text):
    # Visual inspection identifies a form of punctuation spaCy does not
    # recognize: the double dash '--'.  Better get rid of it now!
    text = re.sub(r'--',' ',text)
    text = re.sub("[\[].*?[\]]", "", text)
    text = ' '.join(text.split())
    return text
    
# Load and clean the data.
persuasion = gutenberg.raw('austen-persuasion.txt')
alice = gutenberg.raw('carroll-alice.txt')

# The Chapter indicator is idiosyncratic
persuasion = re.sub(r'Chapter \d+', '', persuasion)
alice = re.sub(r'CHAPTER .*', '', alice)
    
alice = text_cleaner(alice[:int(len(alice)/10)])
persuasion = text_cleaner(persuasion[:int(len(persuasion)/10)])

In [5]:
alice[:1000]

"Alice was beginning to get very tired of sitting by her sister on the bank, and of having nothing to do: once or twice she had peeped into the book her sister was reading, but it had no pictures or conversations in it, 'and what is the use of a book,' thought Alice 'without pictures or conversation?' So she was considering in her own mind (as well as she could, for the hot day made her feel very sleepy and stupid), whether the pleasure of making a daisy-chain would be worth the trouble of getting up and picking the daisies, when suddenly a White Rabbit with pink eyes ran close by her. There was nothing so VERY remarkable in that; nor did Alice think it so VERY much out of the way to hear the Rabbit say to itself, 'Oh dear! Oh dear! I shall be late!' (when she thought it over afterwards, it occurred to her that she ought to have wondered at this, but at the time it all seemed quite natural); but when the Rabbit actually TOOK A WATCH OUT OF ITS WAISTCOAT-POCKET, and looked at it, and th

In [6]:
persuasion

'Sir Walter Elliot, of Kellynch Hall, in Somersetshire, was a man who, for his own amusement, never took up any book but the Baronetage; there he found occupation for an idle hour, and consolation in a distressed one; there his faculties were roused into admiration and respect, by contemplating the limited remnant of the earliest patents; there any unwelcome sensations, arising from domestic affairs changed naturally into pity and contempt as he turned over the almost endless creations of the last century; and there, if every other leaf were powerless, he could read his own history with an interest which never failed. This was the page at which the favourite volume always opened: "ELLIOT OF KELLYNCH HALL. "Walter Elliot, born March 1, 1760, married, July 15, 1784, Elizabeth, daughter of James Stevenson, Esq. of South Park, in the county of Gloucester, by which lady (who died 1800) he has issue Elizabeth, born June 1, 1785; Anne, born August 9, 1787; a still-born son, November 5, 1789; 

In [7]:
# Parse the cleaned novels. This can take a bit.
nlp = spacy.load('en_core_web_sm')
alice_doc = nlp(alice)
persuasion_doc = nlp(persuasion)

In [8]:
alice_doc[:100]

Alice was beginning to get very tired of sitting by her sister on the bank, and of having nothing to do: once or twice she had peeped into the book her sister was reading, but it had no pictures or conversations in it, 'and what is the use of a book,' thought Alice 'without pictures or conversation?' So she was considering in her own mind (as well as she could, for the hot day made her feel very sleepy and stupid), whether the pleasure of making

In [9]:
persuasion_doc[:300]

Sir Walter Elliot, of Kellynch Hall, in Somersetshire, was a man who, for his own amusement, never took up any book but the Baronetage; there he found occupation for an idle hour, and consolation in a distressed one; there his faculties were roused into admiration and respect, by contemplating the limited remnant of the earliest patents; there any unwelcome sensations, arising from domestic affairs changed naturally into pity and contempt as he turned over the almost endless creations of the last century; and there, if every other leaf were powerless, he could read his own history with an interest which never failed. This was the page at which the favourite volume always opened: "ELLIOT OF KELLYNCH HALL. "Walter Elliot, born March 1, 1760, married, July 15, 1784, Elizabeth, daughter of James Stevenson, Esq. of South Park, in the county of Gloucester, by which lady (who died 1800) he has issue Elizabeth, born June 1, 1785; Anne, born August 9, 1787; a still-born son, November 5, 1789; M

In [10]:
# Group into sentences.
alice_sents = [[sent, "Carroll"] for sent in alice_doc.sents]
persuasion_sents = [[sent, "Austen"] for sent in persuasion_doc.sents]

In [11]:
alice_sents

[[Alice was beginning to get very tired of sitting by her sister on the bank, and of having nothing to do: once or twice she had peeped into the book her sister was reading, but it had no pictures or conversations in it, 'and what is the use of a book,' thought Alice 'without pictures or conversation?',
  'Carroll'],
 [So she was considering in her own mind (as well as she could, for the hot day made her feel very sleepy and stupid), whether the pleasure of making a daisy-chain would be worth the trouble of getting up and picking the daisies, when suddenly a White Rabbit with pink eyes ran close by her.,
  'Carroll'],
 [There was nothing so VERY remarkable in that; nor did Alice think it so VERY much out of the way to hear the Rabbit say to itself, ',
  'Carroll'],
 [Oh dear!, 'Carroll'],
 [Oh dear!, 'Carroll'],
 [I shall be late!', 'Carroll'],
 [(when she thought it over afterwards, it occurred to her that she ought to have wondered at this, but at the time it all seemed quite natural

In [12]:
persuasion_sents

[[Sir Walter Elliot, of Kellynch Hall, in Somersetshire, was a man who, for his own amusement, never took up any book but the Baronetage; there he found occupation for an idle hour, and consolation in a distressed one; there his faculties were roused into admiration and respect, by contemplating the limited remnant of the earliest patents; there any unwelcome sensations, arising from domestic affairs changed naturally into pity and contempt as he turned over the almost endless creations of the last century; and there, if every other leaf were powerless, he could read his own history with an interest which never failed.,
  'Austen'],
 [This was the page at which the favourite volume always opened: "ELLIOT OF KELLYNCH HALL.,
  'Austen'],
 [", 'Austen'],
 [Walter Elliot, born March 1, 1760, married, July 15, 1784, Elizabeth, daughter of James Stevenson, Esq. of South Park, in the county of Gloucester, by which lady (who died 1800) he has issue Elizabeth, born June 1, 1785;,
  'Austen'],
 

In [13]:
# Group into sentences.
alice_sents = [[sent, "Carroll"] for sent in alice_doc.sents]
persuasion_sents = [[sent, "Austen"] for sent in persuasion_doc.sents]

# Combine the sentences from the two novels into one data frame.
sentences = pd.DataFrame(alice_sents + persuasion_sents)
sentences.head()

0        1
0  (Alice, was, beginning, to, get, very, tired, ...  Carroll
1  (So, she, was, considering, in, her, own, mind...  Carroll
2  (There, was, nothing, so, VERY, remarkable, in...  Carroll
3                                      (Oh, dear, !)  Carroll
4                                      (Oh, dear, !)  Carroll

Time to **bag some words!**  Since **spaCy has already tokenized and labelled** our data, we can move directly to recording how often various words occur.  We will **exclude stopwords and punctuation**.  In addition, in an attempt to keep our feature space from exploding, we will work with **lemmas (root words)** rather than the raw text terms, and we'll only use the 2000 most common words for each text.

In [14]:
# Utility function to create a list of the 2000 most common words.
def bag_of_words(text):
    
    # Filter out punctuation and stop words.
    allwords = [token.lemma_
                for token in text
                if not token.is_punct
                and not token.is_stop]
    
    # Return the most common words.
    return [item[0] for item in Counter(allwords).most_common(2000)]
    

# Creates a data frame with features for each word in our common word set.
# Each value is the count of the times the word appears in each sentence.
def bow_features(sentences, common_words):
    
    # Scaffold the data frame and initialize counts to zero.
    df = pd.DataFrame(columns=common_words)
    df['text_sentence'] = sentences[0]
    df['text_source'] = sentences[1]
    df.loc[:, common_words] = 0
    
    # Process each row, counting the occurrence of words in each sentence.
    for i, sentence in enumerate(df['text_sentence']):
        
        # Convert the sentence to lemmas, then filter out punctuation,
        # stop words, and uncommon words.
        words = [token.lemma_
                 for token in sentence
                 if (
                     not token.is_punct
                     and not token.is_stop
                     and token.lemma_ in common_words
                 )]
        
        # Populate the row with word counts.
        for word in words:
            df.loc[i, word] += 1
        
        # This counter is just to make sure the kernel didn't hang.
        if i % 50 == 0:
            print("Processing row {}".format(i))
            
    return df

# Set up the bags.
alicewords = bag_of_words(alice_doc)
persuasionwords = bag_of_words(persuasion_doc)

# Combine bags to create a set of unique words.
common_words = set(alicewords + persuasionwords)

In [15]:
len(alicewords)

446

In [16]:
alicewords[:20]

['Alice',
 'think',
 'little',
 'go',
 'way',
 'like',
 'time',
 'find',
 'fall',
 'come',
 'say',
 'wonder',
 'look',
 'door',
 'begin',
 'get',
 'eat',
 'Rabbit',
 'oh',
 'foot']

In [17]:
len(persuasionwords)

1359

In [18]:
persuasionwords[:20]

['Sir',
 'Walter',
 'Elliot',
 'Mr',
 'Lady',
 'Anne',
 'Shepherd',
 'man',
 'father',
 'Russell',
 'Elizabeth',
 'Kellynch',
 'know',
 'house',
 'good',
 'year',
 'think',
 'great',
 'little',
 'Hall']

In [60]:
# Create our data frame with features. This can take a while to run.
word_counts = bow_features(sentences, common_words)
word_counts.head()

Processing row 0
Processing row 500


0  \
courteously                                                    0   
principally                                                    0   
sign                                                           0   
haughty                                                        0   
II                                                             0   
...                                                          ...   
besiege                                                        0   
amusement                                                      0   
involve                                                        0   
text_sentence  (Come, ,, said, my, soul, ,, Such, verses, for...   
text_source                                              Whitman   

                                                               1  \
courteously                                                    0   
principally                                                    0   
sign                                                           1   
haughty                                                        0   
II                                                             0   
...                                                          ...   
besiege                                                        0   
amusement                                                      0   
involve                                                        0   
text_sentence  (That, should, I, after, return, ,, Or, ,, lon...   
text_source                                              Whitman   

                                       2  \
courteously                            0   
principally                            0   
sign                                   0   
haughty                                0   
II                                     0   
...                                  ...   
besiege                                0   
amusement                              0   
involve                                0   
text_sentence  (I, Sing, One's, -, self)   
text_source                      Whitman   

                                                               3  \
courteously                                                    0   
principally                                                    0   
sign                                                           0   
haughty                                                        0   
II                                                             0   
...                                                          ...   
besiege                                                        0   
amusement                                                      0   
involve                                                        0   
text_sentence  (I, sing, ,, a, simple, separate, person, ,, Y...   
text_source                                              Whitman   

                               4  
courteously                    0  
principally                    0  
sign                           0  
haughty                        0  
II                             0  
...                          ...  
besiege                        0  
amusement                      0  
involve                        0  
text_sentence  (En, -, Masse, .)  
text_source              Whitman  

[2374 rows x 5 columns]

In [20]:
word_counts.shape

(444, 1614)

## Trying out BoW

Now let's give the bag of words features a whirl by trying a random forest.

In [21]:
from sklearn import ensemble
from sklearn.model_selection import train_test_split

rfc = ensemble.RandomForestClassifier()
Y = word_counts['text_source']
X = np.array(word_counts.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.4,
                                                    random_state=0)
train = rfc.fit(X_train, y_train)

print('Training set score:', rfc.score(X_train, y_train))
print('\nTest set score:', rfc.score(X_test, y_test))

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\ensemble\forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)


Training set score: 0.9887218045112782

Test set score: 0.848314606741573


In [22]:
rfc

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=10,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [23]:
Y

0      Carroll
1      Carroll
2      Carroll
3      Carroll
4      Carroll
        ...   
439     Austen
440     Austen
441     Austen
442     Austen
443     Austen
Name: text_source, Length: 444, dtype: object

In [24]:
X

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 1, 0, ..., 1, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=object)

In [25]:
print(X_train.shape)
print(y_train.shape)
print(X_test.shape)
print(y_test.shape)

(266, 1612)
(266,)
(178, 1612)
(178,)


Holy overfitting, Batman! Overfitting is a known problem when using bag of words, since it basically involves throwing a massive number of features at a model – some of those features (in this case, word frequencies) will capture noise in the training set. Since overfitting is also a known problem with Random Forests, the divergence between training score and test score is expected.


## BoW with Logistic Regression

Let's try a technique with some protection against overfitting due to extraneous features – logistic regression with ridge regularization (from ridge regression, also called L2 regularization).

In [26]:
from sklearn.linear_model import LogisticRegression
lr = LogisticRegression(penalty='l1')#lasso Regression
train = lr.fit(X_train, y_train)
print(X_train.shape, y_train.shape)
print(lr.score(X_train, y_train))
print(lr.score(X_test, y_test))

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


(266, 1612) (266,)
0.9022556390977443
0.8258426966292135


In [27]:
from sklearn.linear_model import LogisticRegression

lr = LogisticRegression(penalty='l2') # No need to specify l2 as it's the default. But we put it for demonstration.
train = lr.fit(X_train, y_train)
print(X_train.shape, y_train.shape)
print('Training set score:', lr.score(X_train, y_train))
print('\nTest set score:', lr.score(X_test, y_test))

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


(266, 1612) (266,)
Training set score: 0.9774436090225563

Test set score: 0.8707865168539326


Logistic regression performs a bit better than the random forest.  

# BoW with Gradient Boosting

And finally, let's see what gradient boosting can do:

In [28]:
clf = ensemble.GradientBoostingClassifier()
train = clf.fit(X_train, y_train)

print('Training set score:', clf.score(X_train, y_train))
print('\nTest set score:', clf.score(X_test, y_test))

Training set score: 0.9774436090225563

Test set score: 0.8202247191011236


Looks like logistic regression is the winner, but there's room for improvement.

# Same model, new inputs

What if we feed the model a different novel by Jane Austen, like _Emma_?  Will it be able to distinguish Austen from Carroll with the same level of accuracy if we insert a different sample of Austen's writing?

First, we need to process _Emma_ the same way we processed the other data, and combine it with the Alice data. Remember that for computation time concerns, we only took the first tenth of the Alice text. Emma is pretty long. **So in order to get comparable length texts, we take the first sixtieth of Emma**. Again, if you want to experiment, you can take the whole texts of each.

In [61]:
nltk.corpus.gutenberg.fileids()

['austen-emma.txt',
 'austen-persuasion.txt',
 'austen-sense.txt',
 'bible-kjv.txt',
 'blake-poems.txt',
 'bryant-stories.txt',
 'burgess-busterbrown.txt',
 'carroll-alice.txt',
 'chesterton-ball.txt',
 'chesterton-brown.txt',
 'chesterton-thursday.txt',
 'edgeworth-parents.txt',
 'melville-moby_dick.txt',
 'milton-paradise.txt',
 'shakespeare-caesar.txt',
 'shakespeare-hamlet.txt',
 'shakespeare-macbeth.txt',
 'whitman-leaves.txt']

In [29]:
#Clean the Emma data
emma = gutenberg.raw('austen-emma.txt')
emma = re.sub(r'VOLUME \w+', '', emma)
emma = re.sub(r'CHAPTER \w+', '', emma)
emma = text_cleaner(emma[:int(len(emma)/50)])
print(emma[:200])

Emma Woodhouse, handsome, clever, and rich, with a comfortable home and happy disposition, seemed to unite some of the best blessings of existence; and had lived nearly twenty-one years in the world w


In [30]:
 text_cleaner(emma[:int(len(emma)/50)])

'Emma Woodhouse, handsome, clever, and rich, with a comfortable home and happy disposition, seemed to unite some of the best blessings of existence; and had lived nearly twenty-one years in the world with very little to distress or vex her. She was the youngest of the two daughters of a most affectionate, indulgent father; and had, in consequence of'

In [31]:
text_cleaner(emma[:int(len(emma)/80)])

'Emma Woodhouse, handsome, clever, and rich, with a comfortable home and happy disposition, seemed to unite some of the best blessings of existence; and had lived nearly twenty-one years in the world with very little to'

In [32]:
# Clean the Emma data.
emma = gutenberg.raw('austen-emma.txt')
emma = re.sub(r'VOLUME \w+', '', emma)
emma = re.sub(r'CHAPTER \w+', '', emma)
emma = text_cleaner(emma[:int(len(emma)/60)])
print(emma[:200])

Emma Woodhouse, handsome, clever, and rich, with a comfortable home and happy disposition, seemed to unite some of the best blessings of existence; and had lived nearly twenty-one years in the world w


In [33]:
# Parse our cleaned data.
emma_doc = nlp(emma)


In [34]:
emma_doc 

Emma Woodhouse, handsome, clever, and rich, with a comfortable home and happy disposition, seemed to unite some of the best blessings of existence; and had lived nearly twenty-one years in the world with very little to distress or vex her. She was the youngest of the two daughters of a most affectionate, indulgent father; and had, in consequence of her sister's marriage, been mistress of his house from a very early period. Her mother had died too long ago for her to have more than an indistinct remembrance of her caresses; and her place had been supplied by an excellent woman as governess, who had fallen little short of a mother in affection. Sixteen years had Miss Taylor been in Mr. Woodhouse's family, less as a governess than a friend, very fond of both daughters, but particularly of Emma. Between _them_ it was more the intimacy of sisters. Even before Miss Taylor had ceased to hold the nominal office of governess, the mildness of her temper had hardly allowed her to impose any restr

In [35]:
# Group into sentences.
persuasion_sents = [[sent, "Austen"] for sent in persuasion_doc.sents]
emma_sents = [[sent, "Austen"] for sent in emma_doc.sents]

In [36]:
persuasion_sents

[[Sir Walter Elliot, of Kellynch Hall, in Somersetshire, was a man who, for his own amusement, never took up any book but the Baronetage; there he found occupation for an idle hour, and consolation in a distressed one; there his faculties were roused into admiration and respect, by contemplating the limited remnant of the earliest patents; there any unwelcome sensations, arising from domestic affairs changed naturally into pity and contempt as he turned over the almost endless creations of the last century; and there, if every other leaf were powerless, he could read his own history with an interest which never failed.,
  'Austen'],
 [This was the page at which the favourite volume always opened: "ELLIOT OF KELLYNCH HALL.,
  'Austen'],
 [", 'Austen'],
 [Walter Elliot, born March 1, 1760, married, July 15, 1784, Elizabeth, daughter of James Stevenson, Esq. of South Park, in the county of Gloucester, by which lady (who died 1800) he has issue Elizabeth, born June 1, 1785;,
  'Austen'],
 

In [37]:
emma_sents

[[Emma Woodhouse, handsome, clever, and rich, with a comfortable home and happy disposition, seemed to unite some of the best blessings of existence; and had lived nearly twenty-one years in the world with very little to distress or vex her.,
  'Austen'],
 [She was the youngest of the two daughters of a most affectionate, indulgent father; and had, in consequence of her sister's marriage, been mistress of his house from a very early period.,
  'Austen'],
 [Her mother had died too long ago for her to have more than an indistinct remembrance of her caresses; and her place had been supplied by an excellent woman as governess, who had fallen little short of a mother in affection.,
  'Austen'],
 [Sixteen years had Miss Taylor been in Mr. Woodhouse's family, less as a governess than a friend, very fond of both daughters, but particularly of Emma.,
  'Austen'],
 [Between _them, 'Austen'],
 [_, 'Austen'],
 [it was more the intimacy of sisters., 'Austen'],
 [Even before Miss Taylor had ceased t

In [38]:
# Build a new Bag of Words data frame for Emma word counts.
# We'll use the same common words from Alice and Persuasion.
emma_sentences = pd.DataFrame(emma_sents)
emma_bow = bow_features(emma_sentences, common_words)

print('done')

Processing row 0
Processing row 50
Processing row 100
Processing row 150
done


In [39]:
pd.set_option('display.max_columns', None)
#pd.set_option('display.max_rows', None)

In [40]:
emma_bow

Longitude principally II cautious lady soon add quarter scene elude peep  \
0           0           0  0        0    0    0   0       0     0     0    0   
1           0           0  0        0    0    0   0       0     0     0    0   
2           0           0  0        0    0    0   0       0     0     0    0   
3           0           0  0        0    0    0   0       0     0     0    0   
4           0           0  0        0    0    0   0       0     0     0    0   
..        ...         ... ..      ...  ...  ...  ..     ...   ...   ...  ...   
165         0           0  0        0    0    0   0       0     0     0    0   
166         0           0  0        0    0    0   0       0     0     0    0   
167         0           0  0        0    0    0   0       0     0     0    0   
168         0           0  0        0    0    0   0       0     0     0    0   
169         0           0  0        0    0    0   0       0     0     0    0   

    pursuit preserver wait mistake intercourse try turkey contraction  \
0         0         0    0       0           0   0      0           0   
1         0         0    0       0           0   0      0           0   
2         0         0    0       0           0   0      0           0   
3         0         0    0       0           0   0      0           0   
4         0         0    0       0           0   0      0           0   
..      ...       ...  ...     ...         ...  ..    ...         ...   
165       0         0    0       0           0   0      0           0   
166       0         0    0       0           0   0      0           0   
167       0         0    0       0           0   0      0           0   
168       0         0    0       0           0   0      0           0   
169       0         0    0       0           0   0      0           0   

    household precedence fill officer fetch number walk act decency wish  \
0           0          0    0       0     0      0    0   0       0    0   
1           0          0    0       0     0      0    0   0       0    0   
2           0          0    0       0     0      0    0   0       0    0   
3           0          0    0       0     0      0    0   0       0    0   
4           0          0    0       0     0      0    0   0       0    0   
..        ...        ...  ...     ...   ...    ...  ...  ..     ...  ...   
165         0          0    0       0     0      0    0   0       0    0   
166         0          0    0       0     0      0    0   0       0    0   
167         0          0    0       0     0      0    0   0       0    0   
168         0          0    0       0     0      0    0   0       0    0   
169         0          0    0       0     0      0    0   0       0    0   

    small retrenchment apt severe suddenly alienable need modesty usual  \
0       0            0   0      0        0         0    0       0     0   
1       0            0   0      0        0         0    0       0     0   
2       0            0   0      0        0         0    0       0     0   
3       0            0   0      0        0         0    0       0     0   
4       0            0   0      0        0         0    0       0     0   
..    ...          ...  ..    ...      ...       ...  ...     ...   ...   
165     0            0   0      0        0         0    0       0     0   
166     0            0   0      0        0         0    0       0     0   
167     0            0   0      0        0         0    0       0     0   
168     0            0   0      0        0         0    0       0     0   
169     0            0   0      0        0         0    0       0     0   

    remark art House finger duty alarm grove curacy branch rapid HALL forget  \
0        0   0     0      0    0     0     0      0      0     0    0      0   
1        0   0     0      0    0     0     0      0      0     0    0      0   
2        0   0     0      0    0     0     0      0      0     0    0      0   
3        0   0     0      0    0

In [41]:
emma_sentences

0       1
0    (Emma, Woodhouse, ,, handsome, ,, clever, ,, a...  Austen
1    (She, was, the, youngest, of, the, two, daught...  Austen
2    (Her, mother, had, died, too, long, ago, for, ...  Austen
3    (Sixteen, years, had, Miss, Taylor, been, in, ...  Austen
4                                   (Between, _, them)  Austen
..                                                 ...     ...
165  (Mr., Weston, certainly, would, never, marry, ...  Austen
166  (Some, people, even, talked, of, a, promise, t...  Austen
167  (All, manner, of, solemn, nonsense, was, talke...  Austen
168                                                (")  Austen
169  (Ever, since, the, day, about, four, years, ag...  Austen

[170 rows x 2 columns]

In [42]:
# Now we can model it!
# Let's use logistic regression again.

# Combine the Emma sentence data with the Alice data from the test set.
X_Emma_test = np.concatenate((
    X_train[y_train[y_train=='Carroll'].index],
    emma_bow.drop(['text_sentence','text_source'], 1)
), axis=0)
y_Emma_test = pd.concat([y_train[y_train=='Carroll'],
                         pd.Series(['Austen'] * emma_bow.shape[0])])

# Model.
print('\nTest set score:', lr.score(X_Emma_test, y_Emma_test))
lr_Emma_predicted = lr.predict(X_Emma_test)
pd.crosstab(y_Emma_test, lr_Emma_predicted)


Test set score: 0.7073170731707317


col_0    Austen  Carroll
row_0                   
Austen      155       15
Carroll      57       19

In [43]:
X_Emma_test

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=object)

In [44]:
y_Emma_test

116    Carroll
120    Carroll
112    Carroll
126    Carroll
33     Carroll
        ...   
165     Austen
166     Austen
167     Austen
168     Austen
169     Austen
Length: 246, dtype: object

Well look at that!  NLP approaches are generally effective on the same type of material as they were trained on. It looks like this model is actually able to differentiate multiple works by Austen from Alice in Wonderland.  Now the question is whether the model is very good at identifying Austen, or very good at identifying Alice in Wonderland, or both...

# Challenge 0:

Recall that the logistic regression model's best performance on the test set was 93%.  See what you can do to improve performance.  Suggested avenues of investigation include: Other modeling techniques (SVM?), making more features that take advantage of the spaCy information (include grammar, phrases, POS, etc), making sentence-level features (number of words, amount of punctuation), or including contextual information (length of previous and next sentences, words repeated from one sentence to the next, etc), and anything else your heart desires.  Make sure to design your models on the test set, or use cross_validation with multiple folds, and see if you can get accuracy above 90%.  

# Challenge 1:
Find out whether your new model is good at identifying Alice in Wonderland vs any other work, Persuasion vs any other work, or Austen vs any other work.  This will involve pulling a new book from the Project Gutenberg corpus (print(gutenberg.fileids()) for a list) and processing it.

Record your work for each challenge in a notebook and submit it below.

# Challenge 0:

Recall that the logistic regression model's best performance on the test set was 93%.  See what you can do to improve performance.  Suggested avenues of investigation include: Other modeling techniques (SVM?), making more features that take advantage of the spaCy information (include grammar, phrases, POS, etc), making sentence-level features (number of words, amount of punctuation), or including contextual information (length of previous and next sentences, words repeated from one sentence to the next, etc), and anything else your heart desires.  Make sure to design your models on the test set, or use cross_validation with multiple folds, and see if you can get accuracy above 90%. 

## Try SVM

In [45]:
from sklearn.svm import SVC

svc = SVC()
train = svc.fit(X_train, y_train)
print(X_train.shape, y_train.shape)
print('Training set score:', svc.score(X_train, y_train))
print('\nTest set score:', svc.score(X_test, y_test))

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)


(266, 1612) (266,)
Training set score: 0.7142857142857143

Test set score: 0.702247191011236


### Add punctuation to features
Adds 13 columns

In [46]:
# Utility function to create a list of the 2000 most common words.
def words_punct(text):
    
    # Filter out stop words.
    allwords = [token.lemma_
                for token in text
                if not token.is_stop
                ]
    
    # Return the most common words.
    return [item[0] for item in Counter(allwords).most_common(2000)]
    

# Creates a data frame with features for each word in our common word set.
# Each value is the count of the times the word appears in each sentence.
def bow_features(sentences, common_words):
    
    # Scaffold the data frame and initialize counts to zero.
    df = pd.DataFrame(columns=common_words)
    df['text_sentence'] = sentences[0]
    df['text_source'] = sentences[1]
    df.loc[:, common_words] = 0
    
    # Process each row, counting the occurrence of words in each sentence.
    for i, sentence in enumerate(df['text_sentence']):
        
        # Convert the sentence to lemmas, then filter out punctuation,
        # stop words, and uncommon words.
        words = [token.lemma_
                 for token in sentence
                 if (
                     not token.is_stop
                     and token.lemma_ in common_words
                 )]
        
        # Populate the row with word counts.
        for word in words:
            df.loc[i, word] += 1
        
        # This counter is just to make sure the kernel didn't hang.
        if i % 500 == 0:
            print("Processing row {}".format(i))
            
    return df

# Set up the bags.
alicewords_punct = words_punct(alice_doc)
persuasionwords_punct = words_punct(persuasion_doc)

# Combine bags to create a set of unique words.
common_words_punct = set(alicewords_punct + persuasionwords_punct)

# Create data frame with features. This can take a while
word_counts_punct = bow_features(sentences, common_words_punct)
word_counts_punct.head()

Processing row 0


Longitude principally II cautious lady soon add quarter scene elude peep  \
0         0           0  0        0    0    0   0       0     0     0    1   
1         0           0  0        0    0    0   0       0     0     0    0   
2         0           0  0        0    0    0   0       0     0     0    0   
3         0           0  0        0    0    0   0       0     0     0    0   
4         0           0  0        0    0    0   0       0     0     0    0   

  pursuit preserver wait mistake intercourse try turkey contraction household  \
0       0         0    0       0           0   0      0           0         0   
1       0         0    0       0           0   0      0           0         0   
2       0         0    0       0           0   0      0           0         0   
3       0         0    0       0           0   0      0           0         0   
4       0         0    0       0           0   0      0           0         0   

  precedence fill officer fetch number walk act decency wish small  \
0          0    0       0     0      0    0   0       0    0     0   
1          0    0       0     0      0    0   0       0    0     0   
2          0    0       0     0      0    0   0       0    0     0   
3          0    0       0     0      0    0   0       0    0     0   
4          0    0       0     0      0    0   0       0    0     0   

  retrenchment apt severe suddenly alienable need modesty usual remark art  \
0            0   0      0        0         0    0       0     0      0   0   
1            0   0      0        1         0    0       0     0      0   0   
2            0   0      0        0         0    0       0     0      0   0   
3            0   0      0        0         0    0       0     0      0   0   
4            0   0      0        0         0    0       0     0      0   0   

  House finger duty alarm grove curacy branch rapid HALL forget set dining  \
0     0      0    0     0     0      0      0     0    0      0   0      0   
1     0      0    0     0     0      0      0     0    0      0   0      0   
2     0      0    0     0     0      0      0     0    0      0   0      0   
3     0      0    0     0     0      0      0     0    0      0   0      0   
4     0      0    0     0     0      0      0     0    0      0   0      0   

  ready hasten croquet Mrs frost gift money devise deal foot gentleman  \
0     0      0       0   0     0    0     0      0    0    0         0   
1     0      0       0   0     0    0     0      0    0    0         0   
2     0      0       0   0     0    0     0      0    0    0         0   
3     0      0       0   0     0    0     0      0    0    0         0   
4     0      0       0   0     0    0     0      0    0    0         0   

  nonsense mention wife eat flushed especially observance gratitude short  \
0        0       0    0   0       0          0          0         0     0   
1        0       0    0   0       0          0          0         0     0   
2        0       0    0   0       0          0          0         0     0   
3        0       0    0   0       0          0          0         0     0   
4        0       0    0   0       0          0          0         0     0   

  lord Gloucester 1800 conference believe box form vary previous commander  \
0    0          0    0          0       0   0    0    0        0         0   
1    0          0    0          0       0   0    0    0        0         0   
2    0          0    0          0       0   0    0    0        0         0   
3    0          0    0          0       0   0    0    0        0         0   
4    0          0    0          0       0   0    0    0        0         0   

  John choice fare blow atmosphere freely anticipate miserably room method  \
0    0      0    0    0          0      0          0         0    0      0   
1    0      0    0    0          0      0          0         0    0      0   
2    0      0    0    0          0      0          0         0    0      0  

In [63]:
X.shape

(613, 2372)

In [65]:
Y.shape


(613,)

In [47]:
# Test new features using best model from above (logistic)

Y = word_counts_punct['text_source']
X = word_counts_punct.drop(['text_sentence', 'text_source'], 1)

# Split

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.4,
                                                    random_state=0)

lr = LogisticRegression()
lr.fit(X_train, y_train)
print(X_train.shape, y_train.shape)
print('Training set score:', lr.score(X_train, y_train))
print('\nTest set score:', lr.score(X_test, y_test))

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


(266, 1625) (266,)
Training set score: 0.981203007518797

Test set score: 0.9325842696629213


#### Adding punctuation increase accuracy from 70% to 93%.

# Challenge 1:
Find out whether your new model is good at identifying Alice in Wonderland vs any other work, Persuasion vs any other work, or Austen vs any other work.  This will involve pulling a new book from the Project Gutenberg corpus (print(gutenberg.fileids()) for a list) and processing it.

In [48]:
gutenberg.fileids()

['austen-emma.txt',
 'austen-persuasion.txt',
 'austen-sense.txt',
 'bible-kjv.txt',
 'blake-poems.txt',
 'bryant-stories.txt',
 'burgess-busterbrown.txt',
 'carroll-alice.txt',
 'chesterton-ball.txt',
 'chesterton-brown.txt',
 'chesterton-thursday.txt',
 'edgeworth-parents.txt',
 'melville-moby_dick.txt',
 'milton-paradise.txt',
 'shakespeare-caesar.txt',
 'shakespeare-hamlet.txt',
 'shakespeare-macbeth.txt',
 'whitman-leaves.txt']

In [49]:
# Grab Whitman, clean and process
whitman = gutenberg.raw('whitman-leaves.txt')
whitman = re.sub(r'VOLUME \w+', '', whitman)
whitman = re.sub(r'CHAPTER \w+', '', whitman)
whitman = text_cleaner(whitman)
print(whitman[:200])

Come, said my soul, Such verses for my Body let us write, (for we are one,) That should I after return, Or, long, long hence, in other spheres, There to some group of mates the chants resuming, (Tally


In [50]:
# Parse into doc using SpaCy
whitman_doc = nlp(whitman[0:30000])

### Setup and run model: Alice vs. Whitman

Model appears equally effective at identifying Alice vs. Whitman Leaves.

In [51]:
# Bag words
whitmanwords_punct = words_punct(whitman_doc)
alicewords_punct = words_punct(alice_doc)

# Combine Whitman and Alice bags
common_words = set(whitmanwords_punct + alicewords_punct)

# Group into sentences
whitman_sents = [[sent, 'Whitman'] for sent in whitman_doc.sents]

# Combine Whitman and Alice sentences
sentences = pd.DataFrame(whitman_sents + alice_sents)

# Get BoW Features
word_counts = bow_features(sentences, common_words)

Processing row 0


In [70]:
common_words

{'courteously',
 'Longitude',
 'sign',
 'haughty',
 'Illinois',
 'orbic',
 'philosoph',
 'dolce',
 'soon',
 'add',
 'hatter',
 'genius',
 'winner',
 'manly',
 'elude',
 'peep',
 'thither',
 'wait',
 'onward',
 'countenance',
 'translatress',
 'river',
 'silent',
 'try',
 'turkey',
 'Massachusetts',
 'fill',
 'press',
 'race',
 "wish'd",
 'walk',
 'act',
 'concentrate',
 'wish',
 'comrade',
 'beef',
 'small',
 'mystery',
 "ask'd",
 'substance',
 'suddenly',
 'backward',
 'antique',
 'need',
 'usual',
 'art',
 'hemp',
 'finger',
 'Whitman',
 'ye',
 'perennial',
 'curve',
 'peak',
 'behold',
 'feed',
 'forget',
 'set',
 'ready',
 'croquet',
 'marche',
 'gift',
 'human',
 'deal',
 'fuel',
 'foot',
 'nonsense',
 'wife',
 'eat',
 'aloft',
 'retreat',
 'grass',
 'globe',
 'short',
 'retrospective',
 'ocean',
 'cleave',
 'believe',
 'box',
 'form',
 'vary',
 'commander',
 'eastern',
 'resplendent',
 'blow',
 'subtle',
 'fulfil',
 'century',
 'rest',
 'diet',
 'report',
 'fortunately',
 'jump',

In [71]:
sentences

0        1
0    (Come, ,, said, my, soul, ,, Such, verses, for...  Whitman
1    (That, should, I, after, return, ,, Or, ,, lon...  Whitman
2                            (I, Sing, One's, -, self)  Whitman
3    (I, sing, ,, a, simple, separate, person, ,, Y...  Whitman
4                                    (En, -, Masse, .)  Whitman
..                                                 ...      ...
422  (I, wonder, if, I, 've, been, changed, in, the...  Carroll
423  (Let, me, think, :, was, I, the, same, when, I...  Carroll
424  (I, almost, think, I, can, remember, feeling, ...  Carroll
425  (But, if, I, 'm, not, the, same, ,, the, next,...  Carroll
426                                               (Ah)  Carroll

[427 rows x 2 columns]

In [72]:
word_counts

courteously Longitude sign haughty Illinois orbic philosoph dolce soon  \
0             0         0    0       0        0     0         0     0    0   
1             0         0    1       0        0     0         0     0    0   
2             0         0    0       0        0     0         0     0    0   
3             0         0    0       0        0     0         0     0    0   
4             0         0    0       0        0     0         0     0    0   
..          ...       ...  ...     ...      ...   ...       ...   ...  ...   
422           0         0    0       0        0     0         0     0    0   
423           0         0    0       0        0     0         0     0    0   
424           0         0    0       0        0     0         0     0    0   
425           0         0    0       0        0     0         0     0    0   
426           0         0    0       0        0     0         0     0    0   

    add hatter genius winner manly elude peep thither wait onward countenance  \
0     0      0      0      0     0     0    0       0    0      0           0   
1     0      0      0      0     0     0    0       0    0      0           0   
2     0      0      0      0     0     0    0       0    0      0           0   
3     0      0      0      0     0     0    0       0    0      0           0   
4     0      0      0      0     0     0    0       0    0      0           0   
..   ..    ...    ...    ...   ...   ...  ...     ...  ...    ...         ...   
422   0      0      0      0     0     0    0       0    0      0           0   
423   0      0      0      0     0     0    0       0    0      0           0   
424   0      0      0      0     0     0    0       0    0      0           0   
425   0      0      0      0     0     0    0       0    0      0           0   
426   0      0      0      0     0     0    0       0    0      0           0   

    translatress river silent try turkey Massachusetts fill press race wish'd  \
0              0     0      0   0      0             0    0     0    0      0   
1              0     0      0   0      0             0    0     0    0      0   
2              0     0      0   0      0             0    0     0    0      0   
3              0     0      0   0      0             0    0     0    0      0   
4              0     0      0   0      0             0    0     0    0      0   
..           ...   ...    ...  ..    ...           ...  ...   ...  ...    ...   
422            0     0      0   0      0             0    0     0    0      0   
423            0     0      0   0      0             0    0     0    0      0   
424            0     0      0   0      0             0    0     0    0      0   
425            0     0      0   0      0             0    0     0    0      0   
426            0     0      0   0      0             0    0     0    0      0   

    walk act concentrate wish comrade beef small mystery ask'd substance  \
0      0   0           0    0       0    0     0       0     0         0   
1      0   0           0    0       0    0     0       0     0         0   
2      0   0           0    0       0    0     0       0     0         0   
3      0   0           0    0       0    0     0       0     0         0   
4      0   0           0    0       0    0     0       0     0         0   
..   ...  ..         ...  ...     ...  ...   ...     ...   ...       ...   
422    0   0           0    0       0    0     0       0     0         0   
423    0   0           0    0       0    0     0       0     0         0   
424    0   0           0    0       0    0     0       0     0         0   
425    0   0           0    0       0    0     0       0     0         0   
426    0   0           0    0       0    0     0       0     0         0   

    suddenly backward antique need usual art hemp finger Whitman ye perennial  \
0          0        0       0    0     0   0    0      0       0  0         0   
1          0        0       0    0     0   0  

In [52]:
Y = word_counts['text_source']
X = word_counts.drop(['text_sentence', 'text_source'], 1)

In [53]:
Y

0      Whitman
1      Whitman
2      Whitman
3      Whitman
4      Whitman
        ...   
422    Carroll
423    Carroll
424    Carroll
425    Carroll
426    Carroll
Name: text_source, Length: 427, dtype: object

In [55]:
X.shape

(427, 1613)

In [68]:
from sklearn.model_selection import cross_val_score
print('Scores:', cross_val_score(lr, X, Y, cv = 5).mean())

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be ch

Scores: 0.9069305611088898


In [69]:
from sklearn.model_selection import cross_val_score
print('Scores:', cross_val_score(lr, X, Y, cv=5))
print('Avg:', np.mean(cross_val_score(lr, X, Y, cv=5)))

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be ch

Scores: [0.93495935 0.93495935 0.90243902 0.8442623  0.91803279]


C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be ch

Avg: 0.9069305611088898


### Setup and run model: Persuasion vs Whitman

The model is still good at identifying Austen's Persuasion vs. Whitman's Leaves, although there is quite a bit more variation between folds compared to Whitman vs. Alice.

In [73]:
# Combine Whitman and Persuasion bags
common_words = set(whitmanwords_punct + persuasionwords_punct)

# Combine Whitman and Persuasion sentences
sentences = pd.DataFrame(whitman_sents + persuasion_sents)

# Get BoW Features
word_counts = bow_features(sentences, common_words)

Processing row 0
Processing row 500


In [58]:
Y = word_counts['text_source']
X = word_counts.drop(['text_sentence', 'text_source'], 1)

In [59]:
from sklearn.model_selection import cross_val_score
print('Scores:', cross_val_score(lr, X, Y, cv=5))
print('Avg:', np.mean(cross_val_score(lr, X, Y, cv=5)))

C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be ch

Scores: [0.93495935 0.93495935 0.90243902 0.8442623  0.91803279]


C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\catan\.conda\envs\catanEnv\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be ch

Avg: 0.9069305611088898
